<a href="https://colab.research.google.com/github/RAK789266/http-localhost-8888-notebooks-Untitled13.ipynb-kernel_name-python3/blob/main/Untitled24.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [2]:
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go


In [3]:
from google.colab import files
files.upload()

Saving Competition_Data.csv to Competition_Data.csv


{'Competition_Data.csv': b'Index,Fiscal_Week_ID,Store_ID,Item_ID,Price,Item_Quantity,Sales_Amount_No_Discount,Sales_Amount,Competition_Price\n0,2019-11,store_459,item_526,134.49,435,4716.74,11272.59,206.44\n1,2019-11,store_459,item_526,134.49,435,4716.74,11272.59,158.01\n2,2019-11,store_459,item_526,134.49,435,4716.74,11272.59,278.03\n3,2019-11,store_459,item_526,134.49,435,4716.74,11272.59,222.66\n4,2019-11,store_459,item_526,134.49,435,4716.74,11272.59,195.32\n5,2019-11,store_459,item_526,134.49,435,4716.74,11272.59,108.75\n6,2019-11,store_459,item_526,134.49,435,4716.74,11272.59,219.64\n7,2019-11,store_459,item_526,134.49,435,4716.74,11272.59,100.11\n8,2019-11,store_459,item_526,134.49,435,4716.74,11272.59,86.1\n9,2019-11,store_459,item_526,134.49,435,4716.74,11272.59,231.21\n10,2019-11,store_709,item_526,136.79,459,4890.43,11545.08,206.44\n11,2019-11,store_709,item_526,136.79,459,4890.43,11545.08,158.01\n12,2019-11,store_709,item_526,136.79,459,4890.43,11545.08,278.03\n13,2019-11,s

In [23]:
data = pd.read_csv('Competition_Data.csv')
print(data.head())

   Index Fiscal_Week_ID   Store_ID   Item_ID   Price  Item_Quantity  \
0      0        2019-11  store_459  item_526  134.49            435   
1      1        2019-11  store_459  item_526  134.49            435   
2      2        2019-11  store_459  item_526  134.49            435   
3      3        2019-11  store_459  item_526  134.49            435   
4      4        2019-11  store_459  item_526  134.49            435   

   Sales_Amount_No_Discount  Sales_Amount  Competition_Price  
0                   4716.74      11272.59             206.44  
1                   4716.74      11272.59             158.01  
2                   4716.74      11272.59             278.03  
3                   4716.74      11272.59             222.66  
4                   4716.74      11272.59             195.32  


In [25]:
# calculate the percentage change in the price and quality
data['Price_change'] = data.groupby(['Store_ID', 'Item_ID'])['Price'].pct_change()

data['Quality_Change'] = data.groupby(['Store_ID', 'Item_ID'])['Item_Quantity'].pct_change()

# calculate the price elasticity of demand

data['PED'] = data['Quality_Change']/data['Price_change']

data.replace([float('inf'), -float('inf')], float('nan'), inplace=True) # change infinity value to nan
data.dropna(subset=['PED'], inplace=True)

# summary statistics for ped

ped_summary = data['PED'].describe()
print(ped_summary)

count    8234.000000
mean       -0.461013
std        35.573810
min     -1455.268409
25%        -0.796818
50%         0.000000
75%         0.765515
max      1127.613636
Name: PED, dtype: float64


The mean PED is approximately -0.35, which indicates that on average, the demand is slightly inelastic, meaning a 1% increase in price results in a 0.35% decrease in quantity demanded.


Now, let’s have a look at the relationship between the price changes and the change in the quantity demanded in the market:

In [28]:
fig_scatter = px.scatter(data, x='Price_change', y='Quality_Change', title='Price Change vs Quantity Change',
                         labels={'Price_change': 'Price Change (%)', 'Quality_Change': 'Quantity Change (%)'})
fig_scatter.update_traces(marker=dict(color='green', opacity=0.5))
fig_scatter.update_layout(xaxis_title='Price Change (%)', yaxis_title='Quantity Change (%)',
                          template='plotly_white')
fig_scatter.show()

The scatter plot reveals that most data points are concentrated around the origin, which indicates that many products experience minimal changes in quantity demanded despite price changes. It suggests that the demand for these products is generally inelastic. However, there are also some points scattered further away from the origin, particularly in areas with positive price changes, which indicate that certain products have more elastic demand, where quantity responds more noticeably to price changes. Overall, the graph highlights a wide range of demand sensitivities across different products, with a general trend of inelasticity.

In [29]:
# define the data based on PED
elastic_threshold = 1
inelastic_threshold = 0

# segment the data based on PED

data['Segment'] = 'Unitary Elastic'
data.loc[data['PED'] > elastic_threshold, 'Segment'] = 'Elastic'
data.loc[data['PED'] < inelastic_threshold, 'Segment'] = 'Inelastic'
data.loc[data['PED'] == 0, 'Segment'] = 'Zero Elasticity'
data.loc[data['PED'] < 0, 'Segment'] = 'Negative Elasticity'

# count the number of items in each segment

segment_couts = data['Segment'].value_counts()
print(segment_couts)

Segment
Negative Elasticity    4031
Unitary Elastic        2300
Elastic                1740
Zero Elasticity         163
Name: count, dtype: int64


In [34]:
fig_segment = px.scatter(data, x='Price_change', y='Quality_Change', color='Segment', # Changed 'Quality_change' to 'Quality_Change'
                         title='price change vs Quality change across Different market Segment',
                         labels={'Price_Change': 'Price Change (%)', 'Quantity_Change': 'Quantity Change (%)'},
                         color_continuous_scale='Viridis', opacity=0.6)
fig_segment.update_layout(xaxis_title='Price Change (%)', yaxis_title='Quantity Change (%)',
                          template='plotly_white')
fig_segment.show()

The graph depicts the relationship between price change (%) and quantity change (%) across different market segments categorized by elasticity. The segments include:


Negative Elasticity (where price increases lead to quantity decreases)
Unitary Elastic (where price changes result in proportionate quantity changes)
Highly Elastic (where small price changes lead to significant quantity changes)
and Zero Elasticity (where quantity remains unchanged despite price changes)
The scattered points show how each segment responds to price changes, with Negative Elasticity and Highly Elastic segments displaying more sensitivity, as seen in the wider spread of data points, while the Unitary Elastic and Zero Elasticity segments cluster more closely around the origin, indicating more stable or proportionate responses.

Here are concise pricing strategies for each segment identified in the graph:

Negative Elasticity: Focus on reducing prices to stimulate demand, as consumers are sensitive to price increases. Price cuts can lead to significant increases in quantity sold, making up for lower margins.
Unitary Elastic: Maintain stable pricing while focusing on improving product value or differentiating offerings. Since price changes lead to proportional quantity changes, the emphasis should be on balancing price with perceived value to maintain sales volume.
Highly Elastic: Use dynamic pricing strategies, such as promotional discounts or price drops during peak demand periods, to capitalize on the high sensitivity of consumers to price changes. Small price reductions can lead to large increases in sales volume.
Zero Elasticity: Price adjustments are less effective in driving sales changes for this segment. Focus on non-price strategies, such as improving product features, quality, or customer service, to differentiate and capture market share without relying on price changes.
So, this is how we can use the concept of price elasticity of demand for making pricing decisions.